In [1]:
import time
from bs4 import BeautifulSoup
import re
import requests
import itertools
import sys
# from selenium import webdriver
# from webdriver_manager.chrome import ChromeDriverManager
# from selenium.webdriver.chrome.options import Options
import pandas as pd

In [2]:
import json
import scrapy
 
#source: https://dev.to/hellomrspaceman/python-selenium-infinite-scrolling-3o12

def scroll(driver, timeout):
    scroll_pause_time = timeout

    # Get scroll height
    last_height = driver.execute_script("return document.body.scrollHeight")

    while True:
        # Scroll down to bottom
        driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")

        # Wait to load page
        time.sleep(scroll_pause_time)

        # Calculate new scroll height and compare with last scroll height
        new_height = driver.execute_script("return document.body.scrollHeight")
        if new_height == last_height:
            # If heights are the same it will exit the function
            break
        last_height = new_height

# options = Options()

# options.set_preference('permissions.default.image', 2)
# options.set_preference('dom.ipc.plugins.enabled.libflashplayer.so', False)


def all_links(url):
    # Setup the driver. This one uses firefox with some options and a path to the geckodriver
    driver = webdriver.Chrome('/Users/sally/.wdm/drivers/chromedriver/83.0.4103.39/mac64/chromedriver')
    # implicitly_wait tells the driver to wait before throwing an exception
    driver.implicitly_wait(30)
    # driver.get(url) opens the page
    driver.get(url)
    # This starts the scrolling by passing the driver and a timeout
    scroll(driver, 5)
    # Once scroll returns bs4 parsers the page_source
    soup_a = BeautifulSoup(driver.page_source, 'lxml')
    # Them we close the driver as soup_a is storing the page source
    driver.close()

    # Empty array to store the links
    links = []

    # Looping through all the a elements in the page source
    for link in soup_a.find_all('div', {'class':'row artwork-component__content'}):
        # link.get('href') gets the href/url out of the a element
        try:
            links.append([link.find('a',attrs = 'artwork-header__title').contents[0],
                link.find('a',attrs = {'class':'artwork-header__price'}).contents[0].strip('\n').strip('$'),
                 link.find('a',attrs = {'class':None}).contents[0].strip('\n'),
                link.find('a',attrs = {'class':"artwork-header__title"})['href']])
        except:
            pass

    return links


ModuleNotFoundError: No module named 'scrapy'

In [201]:
out = all_links('https://www.seditionart.com/artworks/title/asc/curated?page=16&perPage=400')

In [229]:
out1 = all_links('https://www.seditionart.com/artworks/title/asc/open_platform')

[['_031214d',
  '8',
  'r1ft router',
  'https://www.seditionart.com/r1ft-router/_031214d-1'],
 ['_DSC0888',
  '8',
  'esteban salino tarditti',
  'https://www.seditionart.com/esteban-salino-tarditti-1/_dsc0888-1'],
 ['_DSC1149',
  '8',
  'esteban salino tarditti',
  'https://www.seditionart.com/esteban-salino-tarditti-1/_dsc1149-1'],
 ['_DSC8373',
  '8',
  'esteban salino tarditti',
  'https://www.seditionart.com/esteban-salino-tarditti-1/_dsc8373'],
 ['- Meditation 09 - Human and nature 2015 -',
  '8',
  'Jean-François Réveillard .JfR.',
  'https://www.seditionart.com/jean-francois-reveillard/meditation-09-human-and-nature-2015'],
 ['... so you really?!',
  '20',
  'Brut Carniollus',
  'https://www.seditionart.com/brut-carniollus/so-you-really-1'],
 ['“Carrier of Time"',
  '10',
  'Olivia Barrionuevo-Minkin',
  'https://www.seditionart.com/olivia-barrionuevo-minkin/carrier-of-time'],
 ['[commercial wallpaper] bauernmild',
  '8',
  'Matthias Fitz',
  'https://www.seditionart.com/matth

In [231]:
df = pd.DataFrame(out,columns = ["Name","Cost","Author","Link"])
df1 = pd.DataFrame(out1,columns = ["Name","Cost","Author","Link"])

In [233]:
works = pd.concat([df,df1])

In [235]:
desc = []
for i in works['Link']:
    test = BeautifulSoup(requests.get(i).content, 'html.parser')
    print(test.find('div',attrs = {'class':"excerpt__content text-content artwork-description"}).text.replace('\n',''))
    desc.append(test.find('div',attrs = {'class':"excerpt__content text-content artwork-description"}).text.replace('\n',''))

An examination of contemporary life in Western culture shows how completely our world has been influenced by digital technology and the World Wide Web. The Internet and digital technology have moved from the periphery to the forefront of human interaction, and continue to become ever more entrenched in our daily lives. Mark Dorf is interested in the ways in which we have become dependent upon this technology; to what extent we rely upon the digital realm to navigate our lives, and how this reliance affects our perception of the world around us socially, emotionally, and physically. It is no longer about logging on or off, but rather living within and in harmony with the realms and constructs of the digital world for our newest generation of inhabitants.For Sedition, Dorf presents two limited editions from his //_PATH series composed of photography and moving images. In //_PATH the artist explores these ideas through digital photography, collage, 3D rendering, and primitive 3D scanning 

In [238]:
works['desc'] = desc

In [239]:
works
# test = BeautifulSoup(requests.get("https://www.seditionart.com/mark-dorf/_path-untitled13").content, 'html.parser')
# desc = test.find('div',attrs = {'class':"excerpt__content text-content artwork-description"}).text.replace('\n','')


Name Cost        Author  \
0                         //_path/untitled13   22     Mark Dorf   
1                          //_path/untitled9   24     Mark Dorf   
2     #NewAesthetic TV (Extended Play Remix)   30  Mark Amerika   
3                               1,000 Pounds   30   Sui Jianguo   
4                         100% Gray Coverage   35    Casey Reas   
...                                      ...  ...           ...   
1858             字苗-冥王星 Universe-Pluto(part)    8    Sting Chen   
1859              字苗-金星 Universe-Venus(part)    8    Sting Chen   
1860                                  我们在看着你    8        Type-O   
1861                                    無二無別   20   viadmun low   
1862                                    音の彫刻   15   Tony Broyez   

                                                   Link  \
0     https://www.seditionart.com/mark-dorf/_path-un...   
1     https://www.seditionart.com/mark-dorf/_path-un...   
2     https://www.seditionart.com/mark-amerika/newae...   
3     https://www.seditionart.com/sui_jianguo/1_000_...   
4     https://www.seditionart.com/casey_reas/100_gra...   
...                                                 ...   
1858  https://www.seditionart.com/sting-chen/univers...   
1859  https://www.seditionart.com/sting-chen/univers...   
1860  https://www.seditionart.com/type-o/b7a13c95-b1...   
1861  https://www.seditionart.com/viadmun_low_1/555b...   
1862  https://www.seditionart.com/tony-broyez/3c304e...   

                                                   desc  
0     An examination of contemporary life in Western...  
1     An examination of contemporary life in Western...  
2     Mark Amerika’s short video piece #NewAesthetic...  
3     It certainly is not easy for a digital two-dim...  
4     Casey Reas’ 10 minutes digital video-piece 100...  
...                                                 ...  
1858                        字苗-冥王星 Universe-Pluto(part)  
1859                         字苗-金星 Universe-Venus(part)  
1860  我们在看着你 'we are watching you' simple Chinese ve...  
1861  2013Mango leaf specimens無二無別  No difference Is...  
1862  音の彫刻 (literally 'sculpture of sound') is part ...  

[2684 rows x 5 columns]

In [245]:
#works.to_csv("Art.csv",index=False)

In [3]:
df = pd.read_csv("Art.csv")

In [110]:
df[df['Cost'] == 'Not for sale']

52

In [99]:
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from sklearn.svm import SVC
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.metrics import classification_report, precision_recall_fscore_support
from sklearn.feature_extraction.text import TfidfTransformer

In [3]:
nltk.download('punkt')
nltk.download('stopwords')
tfidf = TfidfVectorizer(sublinear_tf = True, analyzer = 'word', max_features = 2000, tokenizer = word_tokenize)

[nltk_data] Downloading package punkt to /home/s4poon/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /home/s4poon/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [219]:
df['desc'][:int(len(df['desc'])*0.8)].values.astype('U').tolist()

['An examination of contemporary life in Western culture shows how completely our world has been influenced by digital technology and the World Wide Web. The Internet and digital technology have moved from the periphery to the forefront of human interaction, and continue to become ever more entrenched in our daily lives. Mark Dorf is interested in the ways in which we have become dependent upon this technology; to what extent we rely upon the digital realm to navigate our lives, and how this reliance affects our perception of the world around us socially, emotionally, and physically. It is no longer about logging on or off, but rather living within and in harmony with the realms and constructs of the digital world for our newest generation of inhabitants.For Sedition, Dorf presents two limited editions from his //_PATH series composed of photography and moving images. In //_PATH the artist explores these ideas through digital photography, collage, 3D rendering, and primitive 3D scannin

In [56]:
vectorizer = CountVectorizer(max_df=0.85,stop_words = stopwords.words('english'))

In [217]:
words = vectorizer.fit_transform(df['desc'][:int(len(df['desc'])*0.8)].values.astype('U').tolist())
tfidf = TfidfTransformer(smooth_idf = True, use_idf = True)
tfidf.fit(words)

<2147x16304 sparse matrix of type '<class 'numpy.int64'>'
	with 109688 stored elements in Compressed Sparse Row format>

In [100]:
test = df['desc'][int(len(df['desc'])*0.2):].values.astype('U').tolist()

In [107]:
features = vectorizer.get_feature_names()
zero = test[0]
top_words = []
for spot in range(i,len(test)):
    top_5 = []
    doc = test[spot]
    tf_idf_vect = tfidf.transform(vectorizer.transform([doc]))
    sorted_items = sort_coo(tf_idf_vect.tocoo())
    keywords=extract_topn_from_vector(features,sorted_items,5)
    for k in keywords:
        top_5.append(k)
    top_words.append(top_5)

[['colour', 'biederman', 'tint', 'blue', 'phase'],
 ['radiant', 'flaxton', 'sound', 'two', 'exhibitions'],
 ['hart', 'rainy', 'engendered', 'wheels', 'simulated'],
 ['reimagining', 'demand', 'flaxton', 'timeline', 'imagined'],
 ['imagining', 'reimagining', 'imagined', 'venice', 'already'],
 ['net', 'reading', 'lists', 'composting', 'list'],
 ['reconciliation', 'holocaust', 'project', 'ugliness', 'exhibition'],
 ['nan'],
 ['liu', 'warship', 'ye', 'philosophy', 'poles'],
 ['public', 'footage', 'reactionbubble', 'laser', 'wood'],
 ['cornwall', 'twice', 'sea', 'water', 'reflection'],
 ['reincarnation', 'completes', 'russian', 'alienation', 'wallpaper'],
 ['reliquary', 'sawhney', 'nitin', 'benney', 'flame'],
 ['reliquary', 'sawhney', 'nitin', 'benney', 'flame'],
 ['reliquary', 'sawhney', 'nitin', 'benney', 'flame'],
 ['reliquary', 'sawhney', 'nitin', 'benney', 'flame'],
 ['reliquary', 'sawhney', 'nitin', 'benney', 'flame'],
 ['reliquary', 'sawhney', 'nitin', 'benney', 'flame'],
 ['repose', 

In [90]:
tf_idf_vect = tfidf.transform(vectorizer.transform([zero]))

In [91]:
sorted_items = sort_coo(tf_idf_vect.tocoo())

In [92]:
keywords=extract_topn_from_vector(features,sorted_items,5)

In [113]:
# now print the results
# print("\n=====Doc=====")
print(test[10])
print("\n===Keywords===")
for k in keywords:
    print(k)

Liu Ye's Red Warship is a digital reference to Liu's 1997 oil painting, Spirit of the Sea,and comprises many of the themes typical of the artist's oeuvre: we find homage to Piet Mondrian, characters depicted are rendered in a puerile style, we see sailor hats and angel wings simultaneously. It is a prime example of how Liu likes to play between mysterious fantasy and episodes of complex storytelling and art historical references.Liu: "I have an equal passion for fairy tales and philosophy. Fairy tales are full of imagination and sensitivity whereas philosophy requires strict and rational thinking. Fairytales and philosophy represent two extreme poles of thinking. My paintings roam between these poles (...)."The artist explores his feelings of adventure and ambivalence by combining oppositional symbols. In Red Warship, this is highlighted by the work's animation: airplanes cross the sky and the warship slowly moves along the horizon, but the activity is interrupted and contrasted by the

In [68]:
# Source = https://kavita-ganesan.com/extracting-keywords-from-text-tfidf/
# def sort_coo(coo_matrix):
#     tuples = zip(coo_matrix.col, coo_matrix.data)
#     return sorted(tuples, key=lambda x: (x[1], x[0]), reverse=True)
 
def extract_topn_from_vector(feature_names, sorted_items, topn=10):
    """get the feature names and tf-idf score of top n items"""
    
    #use only topn items from vector
    sorted_items = sorted_items[:topn]
 
    score_vals = []
    feature_vals = []
    
    # word index and corresponding tf-idf score
    for idx, score in sorted_items:
        
        #keep track of feature name and its corresponding score
        score_vals.append(round(score, 3))
        feature_vals.append(feature_names[idx])
 
    #create a tuples of feature,score
    #results = zip(feature_vals,score_vals)
    results= {}
    for idx in range(len(feature_vals)):
        results[feature_vals[idx]]=score_vals[idx]
    
    return results

In [112]:
#create training data (personality, preferrences in art) (supervised)
#clustering, dimensionality
#dimensionality reduction > different personality people have > cluster > matching manually to artwork
#Compare with other users

In [152]:
train = BeautifulSoup(requests.get("https://www.saatchiart.com/art/Painting-Decomposed-Light/1046861/3988228/view").content, 'html.parser')

In [178]:
train

<!DOCTYPE html>
<html lang="en"><head><meta content="ie=edge" http-equiv="x-ua-compatible"/><meta content="width=device-width, initial-scale=1.0, maximum-scale=1.0, user-scalable=no" name="viewport"/><meta content="D0TrMFxM-EpPQHRE3_NhEkyr18KTU2oAKWthx_UiPEw" name="google-site-verification"/><style data-styled-components="bsPoxE bKGTYk kFrQGK jmsRni grHWap ewLUfv cEnlRF hSGrfW jHogUX dHdAhW kfkiDV llJOHj cjJLlv gHEHpw fXuysw bUoWyW eFDjkx FLzzN fxzYOM eFiwCq czjRTY jlhiyS gGyMXi jnBzyL kJcruy fdjVkX OWRML jtDtHV jKYDRR cEDvlA KPsjK efvDDC gwDKhJ clVFag hjivzt eiJhto loCjRm dfNAjA daSzlt iIiqTe iViBjr jTkyUN beRwVV iVZUBe fKZDuC saqPZ eTujij caicHM bObvSj mfcPt foOOUV dvgkfA jpdSXi jnZcja kiNGTO hyxdWW gViScZ fpvhcV iEJsMc fbclaH jkccrk dhahuo bGYkHR frSDGO dlPOjJ nqgDg CTZJS hltbnD cyxhyN XTcjh jsPRNI iLXtdz eDGVEy eBQklQ fAkdXG cPLLFH cuQhef iFwfwl kIUkGB jWTnTE fNkpnS ihNJxl ttkWN esUzyD hQhOhY kEiXgR dTfZHa buIXUZ jdFLAJ eVHEot tYesL ckuAgQ bHqSXR cgNBgy bCDscl gAJJEa kSbZLI beVrNN 

In [186]:
keywords = []
for j in range(1,50):
    link = BeautifulSoup(requests.get("https://www.saatchiart.com/paintings/digital?hitsPerPage=100&page=" + str(j)).content, 'html.parser')
    tags = link.find("div",attrs= {'class': "w03luy-2 knZzRu"})
    iterate = tags.findAll('a',attrs = {"alt":None},href=True)
    for i in iterate:
        links = BeautifulSoup(requests.get("https://www.saatchiart.com" + i.get('href')).content, 'html.parser')
        keywords.append(re.findall('"keywords":\[(.*?)\]',str(links))[0])
        

KeyboardInterrupt: 

In [1]:
#from flask import Flask, flash, redirect, render_template, request, session, abort,send_from_directory,send_file
import pandas as pd 
import numpy as np
import json
import xlrd
from sklearn.feature_extraction.text import TfidfVectorizer#Create a flask application
# application= Flask(__name__)#Create an application route
# application.route("/",methods=["GET","POST"])
# Imports - these are all the imports needed for the assignment
%matplotlib inline

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

# Import nltk package 
#   PennTreeBank word tokenizer 
#   English language stopwords
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

# scikit-learn imports
#   SVM (Support Vector Machine) classifer 
#   Vectorizer, which transforms text data into bag-of-words feature
#   TF-IDF Vectorizer that first removes widely used words in the dataset and then transforms test data
#   Metrics functions to evaluate performance
from sklearn.svm import SVC
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.metrics import classification_report, precision_recall_fscore_support

In [101]:
def convert_IE(label):
    if (label == 'Introverted'):
        return 0.0
    elif (label == 'Extraverted'):
        return 1.0
    else:
        return label
def convert_IO(label):
    if (label == 'Intuitive'):
        return 0.0
    elif (label == 'Sensing'):
        return 1.0
    else:
        return label
def convert_TF(label):
    if (label == 'Thinking'):
        return 0.0
    elif (label == 'Feeling'):
        return 1.0
    else:
        return label
def convert_JP(label):
    if (label == 'Judging'):
        return 0.0
    elif (label == 'Perceiving'):
        return 1.0
    else:
        return label

In [116]:
datasource1 = pd.read_csv("Personalities.csv")
df = pd.read_csv("Art.csv")
datasource1

type Introversion/Extraversion Intuitive/Observant Thinking/Feeling  \
0     INFJ               Introverted           Intuitive          Feeling   
1     ENTP               Extraverted           Intuitive         Thinking   
2     INTP               Introverted           Intuitive         Thinking   
3     INTJ               Introverted           Intuitive         Thinking   
4     ENTJ               Extraverted           Intuitive         Thinking   
...    ...                       ...                 ...              ...   
8670  ISFP               Introverted             Sensing          Feeling   
8671  ENFP               Extraverted           Intuitive          Feeling   
8672  INTP               Introverted           Intuitive         Thinking   
8673  INFP               Introverted           Intuitive          Feeling   
8674  INFP               Introverted           Intuitive          Feeling   

     Judging/Perceiving                                              posts  
0               Judging  http://www.youtube.com/watch?v=qsXHcwe3krwIhtt...  
1            Perceiving  I'm finding the lack of me in these posts very...  
2            Perceiving  Good one  _____   https://www.youtube.com/watc...  
3               Judging  Dear INTP,   I enjoyed our conversation the ot...  
4               Judging  You're fired.IThat's another silly misconcepti...  
...                 ...                                                ...  
8670         Perceiving  'https://www.youtube.com/watch?v=t8edHB_h908||...  
8671         Perceiving  'So...if this thread already exists someplace ...  
8672         Perceiving  'So many questions when i do these things.  I ...  
8673         Perceiving  'I am very conflicted right now when it comes ...  
8674         Perceiving  'It has been too long since I have been on per...  

[8675 rows x 6 columns]

In [103]:
train_df = datasource1[['posts','Introversion/Extraversion']]
df['posts'] = df['desc']
test_df = pd.DataFrame(df['posts'])

In [107]:
train_df['Introversion/Extraversion'] = train_df['Introversion/Extraversion'].apply(convert_IE)
# train_df['Intuitive/Observant'] = train_df['Intuitive/Observant'].apply(convert_IO)
# train_df['Thinking/Feeling'] = train_df['Thinking/Feeling'].apply(convert_TF)
# train_df['Judging/Perceiving'] = train_df['Judging/Perceiving'].apply(convert_JP)

/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [108]:
tfidf = TfidfVectorizer(sublinear_tf = True, analyzer = 'word', max_features = 2000, tokenizer = word_tokenize)

In [109]:
MR_tfidf_X = tfidf.fit_transform(train_df['posts']).toarray()

In [110]:
MR_test_tfidf_y

6940              0
6941              0
6942    Extraverted
6943              0
6944              0
           ...     
8670              0
8671    Extraverted
8672              0
8673              0
8674              0
Name: IE, Length: 1735, dtype: object

In [111]:
MR_y = train_df['Introversion/Extraversion']
num_training = int(len(train_df) * 0.8)
num_testing = int(len(train_df) * 0.2)

In [112]:
MR_train_tfidf_X = MR_tfidf_X[:num_training]
MR_train_tfidf_y = MR_y[:num_training]

MR_test_tfidf_X = MR_tfidf_X[num_training:]
MR_test_tfidf_y = MR_y[num_training:]

In [113]:
def train_SVM(X, y, kernel='linear'):
# YOUR CODE HERE
    clf = SVC(kernel = kernel)
    clf.fit(X,y)
    return clf
#raise NotImplementedError()

In [117]:
MR_tfidf_clf = train_SVM(MR_train_tfidf_X,MR_train_tfidf_y.values)

In [118]:
MR_pred_train_tfidf_y = MR_tfidf_clf.predict(MR_train_tfidf_X)
MR_pred_test_tfidf_y = MR_tfidf_clf.predict(MR_test_tfidf_X)

In [ ]:
print(classification_report(MR_train_tfidf_y, MR_pred_train_tfidf_y))

In [ ]:
print(classification_report(MR_test_tfidf_y, MR_pred_test_tfidf_y))

In [119]:
CR_df = pd.concat([train_df,test_df])
CR_df

/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


Introversion/Extraversion  \
0                           0.0   
1                           1.0   
2                           0.0   
3                           0.0   
4                           1.0   
...                         ...   
2679                        NaN   
2680                        NaN   
2681                        NaN   
2682                        NaN   
2683                        NaN   

                                                  posts  
0     http://www.youtube.com/watch?v=qsXHcwe3krwIhtt...  
1     I'm finding the lack of me in these posts very...  
2     Good one  _____   https://www.youtube.com/watc...  
3     Dear INTP,   I enjoyed our conversation the ot...  
4     You're fired.IThat's another silly misconcepti...  
...                                                 ...  
2679                        字苗-冥王星 Universe-Pluto(part)  
2680                         字苗-金星 Universe-Venus(part)  
2681  我们在看着你 'we are watching you' simple Chinese ve...  
2682  2013Mango leaf specimens無二無別  No difference Is...  
2683  音の彫刻 (literally 'sculpture of sound') is part ...  

[11359 rows x 2 columns]

In [120]:
CR_tfidf_X = tfidf.fit_transform(CR_df['posts'].values.astype('U')).toarray()

In [121]:
CR_df["y"] = CR_df['Introversion/Extraversion']

In [122]:
CR_train_X = CR_tfidf_X[~CR_df['y'].isnull()]
CR_train_y = CR_df['y'][~CR_df['y'].isnull()]

In [123]:
CR_clf = train_SVM(CR_train_X,CR_train_y)

In [124]:
CR_pred_train_y = CR_clf.predict(CR_train_X)

In [125]:
len(CR_pred_train_y)

8675

In [126]:
CR_test_X = CR_tfidf_X[CR_df['y'].isnull()]

In [127]:
CR_pred_test_y = CR_clf.predict(CR_test_X)

In [128]:
#df['Introversion/Extraversion'] = CR_pred_test_y
IE_CR_pred_test_y = CR_pred_test_y

In [129]:
print(classification_report(CR_train_y, CR_pred_train_y))

              precision    recall  f1-score   support

         0.0       0.89      0.97      0.93      6676
         1.0       0.88      0.61      0.72      1999

    accuracy                           0.89      8675
   macro avg       0.89      0.79      0.83      8675
weighted avg       0.89      0.89      0.88      8675



In [132]:
train_df = datasource1[['posts','Intuitive/Observant']]
df['posts'] = df['desc']
test_df = pd.DataFrame(df['posts'])
train_df['Intuitive/Observant'] = train_df['Intuitive/Observant'].apply(convert_IO)
MR_y = train_df['Intuitive/Observant']
num_training = int(len(train_df) * 0.8)
num_testing = int(len(train_df) * 0.2)
MR_train_tfidf_X = MR_tfidf_X[:num_training]
MR_train_tfidf_y = MR_y[:num_training]

MR_test_tfidf_X = MR_tfidf_X[num_training:]
MR_test_tfidf_y = MR_y[num_training:]
MR_tfidf_clf = train_SVM(MR_train_tfidf_X,MR_train_tfidf_y.values)
MR_pred_train_tfidf_y = MR_tfidf_clf.predict(MR_train_tfidf_X)
MR_pred_test_tfidf_y = MR_tfidf_clf.predict(MR_test_tfidf_X)
CR_df = pd.concat([train_df,test_df])
CR_df
CR_tfidf_X = tfidf.fit_transform(CR_df['posts'].values.astype('U')).toarray()
CR_df["y"] = CR_df['Intuitive/Observant']
CR_train_X = CR_tfidf_X[~CR_df['y'].isnull()]
CR_train_y = CR_df['y'][~CR_df['y'].isnull()]
CR_clf = train_SVM(CR_train_X,CR_train_y)
CR_pred_train_y = CR_clf.predict(CR_train_X)
CR_test_X = CR_tfidf_X[CR_df['y'].isnull()]
CR_pred_test_y = CR_clf.predict(CR_test_X)
IO_CR_pred_test_y = CR_pred_test_y

/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.
/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:16: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  app.launch_new_instance()


In [133]:
train_df = datasource1[['posts','Thinking/Feeling']]
df['posts'] = df['desc']
test_df = pd.DataFrame(df['posts'])
train_df['Thinking/Feeling'] = train_df['Thinking/Feeling'].apply(convert_TF)
MR_y = train_df['Thinking/Feeling']
num_training = int(len(train_df) * 0.8)
num_testing = int(len(train_df) * 0.2)
MR_train_tfidf_X = MR_tfidf_X[:num_training]
MR_train_tfidf_y = MR_y[:num_training]

MR_test_tfidf_X = MR_tfidf_X[num_training:]
MR_test_tfidf_y = MR_y[num_training:]
MR_tfidf_clf = train_SVM(MR_train_tfidf_X,MR_train_tfidf_y.values)
MR_pred_train_tfidf_y = MR_tfidf_clf.predict(MR_train_tfidf_X)
MR_pred_test_tfidf_y = MR_tfidf_clf.predict(MR_test_tfidf_X)
CR_df = pd.concat([train_df,test_df])
CR_df
CR_tfidf_X = tfidf.fit_transform(CR_df['posts'].values.astype('U')).toarray()
CR_df["y"] = CR_df['Thinking/Feeling']
CR_train_X = CR_tfidf_X[~CR_df['y'].isnull()]
CR_train_y = CR_df['y'][~CR_df['y'].isnull()]
CR_clf = train_SVM(CR_train_X,CR_train_y)
CR_pred_train_y = CR_clf.predict(CR_train_X)
CR_test_X = CR_tfidf_X[CR_df['y'].isnull()]
CR_pred_test_y = CR_clf.predict(CR_test_X)
TF_CR_pred_test_y = CR_pred_test_y

/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.
/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:16: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  app.launch_new_instance()


In [134]:
train_df = datasource1[['posts','Judging/Perceiving']]
df['posts'] = df['desc']
test_df = pd.DataFrame(df['posts'])
train_df['Judging/Perceiving'] = train_df['Judging/Perceiving'].apply(convert_JP)
MR_y = train_df['Judging/Perceiving']
num_training = int(len(train_df) * 0.8)
num_testing = int(len(train_df) * 0.2)
MR_train_tfidf_X = MR_tfidf_X[:num_training]
MR_train_tfidf_y = MR_y[:num_training]

MR_test_tfidf_X = MR_tfidf_X[num_training:]
MR_test_tfidf_y = MR_y[num_training:]
MR_tfidf_clf = train_SVM(MR_train_tfidf_X,MR_train_tfidf_y.values)
MR_pred_train_tfidf_y = MR_tfidf_clf.predict(MR_train_tfidf_X)
MR_pred_test_tfidf_y = MR_tfidf_clf.predict(MR_test_tfidf_X)
CR_df = pd.concat([train_df,test_df])
CR_df
CR_tfidf_X = tfidf.fit_transform(CR_df['posts'].values.astype('U')).toarray()
CR_df["y"] = CR_df['Judging/Perceiving']
CR_train_X = CR_tfidf_X[~CR_df['y'].isnull()]
CR_train_y = CR_df['y'][~CR_df['y'].isnull()]
CR_clf = train_SVM(CR_train_X,CR_train_y)
CR_pred_train_y = CR_clf.predict(CR_train_X)
CR_test_X = CR_tfidf_X[CR_df['y'].isnull()]
CR_pred_test_y = CR_clf.predict(CR_test_X)
JP_CR_pred_test_y = CR_pred_test_y

/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.
/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:16: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  app.launch_new_instance()


In [135]:
JP_CR_pred_test_y

array([1., 1., 1., ..., 1., 1., 1.])

In [136]:
TF_CR_pred_test_y

array([0., 0., 1., ..., 0., 0., 0.])

In [137]:
IO_CR_pred_test_y

array([0., 0., 0., ..., 1., 0., 0.])

In [138]:
IE_CR_pred_test_y

array([0., 0., 0., ..., 0., 0., 0.])

In [139]:
df['Introversion/Extraversion'] = IE_CR_pred_test_y

In [140]:
df['Intuitive/Observant'] = IO_CR_pred_test_y

In [141]:
df['Thinking/Feeling'] = TF_CR_pred_test_y

In [142]:
df['Judging/Perceiving']= JP_CR_pred_test_y

In [143]:
df

Name Cost        Author  \
0                         //_path/untitled13   22     Mark Dorf   
1                          //_path/untitled9   24     Mark Dorf   
2     #NewAesthetic TV (Extended Play Remix)   30  Mark Amerika   
3                               1,000 Pounds   30   Sui Jianguo   
4                         100% Gray Coverage   35    Casey Reas   
...                                      ...  ...           ...   
2679             字苗-冥王星 Universe-Pluto(part)    8    Sting Chen   
2680              字苗-金星 Universe-Venus(part)    8    Sting Chen   
2681                                  我们在看着你    8        Type-O   
2682                                    無二無別   20   viadmun low   
2683                                    音の彫刻   15   Tony Broyez   

                                                   Link  \
0     https://www.seditionart.com/mark-dorf/_path-un...   
1     https://www.seditionart.com/mark-dorf/_path-un...   
2     https://www.seditionart.com/mark-amerika/newae...   
3     https://www.seditionart.com/sui_jianguo/1_000_...   
4     https://www.seditionart.com/casey_reas/100_gra...   
...                                                 ...   
2679  https://www.seditionart.com/sting-chen/univers...   
2680  https://www.seditionart.com/sting-chen/univers...   
2681  https://www.seditionart.com/type-o/b7a13c95-b1...   
2682  https://www.seditionart.com/viadmun_low_1/555b...   
2683  https://www.seditionart.com/tony-broyez/3c304e...   

                                                   desc  \
0     An examination of contemporary life in Western...   
1     An examination of contemporary life in Western...   
2     Mark Amerika’s short video piece #NewAesthetic...   
3     It certainly is not easy for a digital two-dim...   
4     Casey Reas’ 10 minutes digital video-piece 100...   
...                                                 ...   
2679                        字苗-冥王星 Universe-Pluto(part)   
2680                         字苗-金星 Universe-Venus(part)   
2681  我们在看着你 'we are watching you' simple Chinese ve...   
2682  2013Mango leaf specimens無二無別  No difference Is...   
2683  音の彫刻 (literally 'sculpture of sound') is part ...   

                                                  posts  \
0     An examination of contemporary life in Western...   
1     An examination of contemporary life in Western...   
2     Mark Amerika’s short video piece #NewAesthetic...   
3     It certainly is not easy for a digital two-dim...   
4     Casey Reas’ 10 minutes digital video-piece 100...   
...                                                 ...   
2679                        字苗-冥王星 Universe-Pluto(part)   
2680                         字苗-金星 Universe-Venus(part)   
2681  我们在看着你 'we are watching you' simple Chinese ve...   
2682  2013Mango leaf specimens無二無別  No difference Is...   
2683  音の彫刻 (literally 'sculpture of sound') is part ...   

      Introversion/Extraversion  Intuitive/Observant  Thinking/Feeling  \
0                           0.0                  0.0               0.0   
1                           0.0                  0.0               0.0   
2                           0.0                  0.0               1.0   
3                           0.0                  0.0               0.0   
4                           0.0                  0.0               0.0   
...                         ...                  ...               ...   
2679                        0.0                  0.0               1.0   
2680                        0.0                  0.0               1.0   
2681                        0.0                  1.0               0.0   
2682                        0.0                  0.0               0.0   
2683                        0.0                  0.0               0.0   

      Judging/Perceiving  
0                    1.0  
1                    1.0  
2                    1.0  
3                    1.0  
4                    1.0  
...                  ...  
2679                 0.0  
268

In [144]:
def convert_IE(label):
    if (label == 0.0):
        return 'Introverted'
    elif (label == 1.0):
        return 'Extraverted'
    else:
        return label
def convert_IO(label):
    if (label == 0.0):
        return 'Intuitive'
    elif (label == 1.0):
        return 'Sensing'
    else:
        return label
def convert_TF(label):
    if (label == 0.0):
        return 'Thinking'
    elif (label == 1.0):
        return 'Feeling'
    else:
        return label
def convert_JP(label):
    if (label == 0.0):
        return 'Judging'
    elif (label == 1.0):
        return 'Perceiving'
    else:
        return label

In [145]:
df['Introversion/Extraversion'] = df['Introversion/Extraversion'].apply(convert_IE)
df['Intuitive/Observant'] = df['Intuitive/Observant'].apply(convert_IO)
df['Thinking/Feeling'] = df['Thinking/Feeling'].apply(convert_TF)
df['Judging/Perceiving'] = df['Judging/Perceiving'].apply(convert_JP)

In [146]:
df

Name Cost        Author  \
0                         //_path/untitled13   22     Mark Dorf   
1                          //_path/untitled9   24     Mark Dorf   
2     #NewAesthetic TV (Extended Play Remix)   30  Mark Amerika   
3                               1,000 Pounds   30   Sui Jianguo   
4                         100% Gray Coverage   35    Casey Reas   
...                                      ...  ...           ...   
2679             字苗-冥王星 Universe-Pluto(part)    8    Sting Chen   
2680              字苗-金星 Universe-Venus(part)    8    Sting Chen   
2681                                  我们在看着你    8        Type-O   
2682                                    無二無別   20   viadmun low   
2683                                    音の彫刻   15   Tony Broyez   

                                                   Link  \
0     https://www.seditionart.com/mark-dorf/_path-un...   
1     https://www.seditionart.com/mark-dorf/_path-un...   
2     https://www.seditionart.com/mark-amerika/newae...   
3     https://www.seditionart.com/sui_jianguo/1_000_...   
4     https://www.seditionart.com/casey_reas/100_gra...   
...                                                 ...   
2679  https://www.seditionart.com/sting-chen/univers...   
2680  https://www.seditionart.com/sting-chen/univers...   
2681  https://www.seditionart.com/type-o/b7a13c95-b1...   
2682  https://www.seditionart.com/viadmun_low_1/555b...   
2683  https://www.seditionart.com/tony-broyez/3c304e...   

                                                   desc  \
0     An examination of contemporary life in Western...   
1     An examination of contemporary life in Western...   
2     Mark Amerika’s short video piece #NewAesthetic...   
3     It certainly is not easy for a digital two-dim...   
4     Casey Reas’ 10 minutes digital video-piece 100...   
...                                                 ...   
2679                        字苗-冥王星 Universe-Pluto(part)   
2680                         字苗-金星 Universe-Venus(part)   
2681  我们在看着你 'we are watching you' simple Chinese ve...   
2682  2013Mango leaf specimens無二無別  No difference Is...   
2683  音の彫刻 (literally 'sculpture of sound') is part ...   

                                                  posts  \
0     An examination of contemporary life in Western...   
1     An examination of contemporary life in Western...   
2     Mark Amerika’s short video piece #NewAesthetic...   
3     It certainly is not easy for a digital two-dim...   
4     Casey Reas’ 10 minutes digital video-piece 100...   
...                                                 ...   
2679                        字苗-冥王星 Universe-Pluto(part)   
2680                         字苗-金星 Universe-Venus(part)   
2681  我们在看着你 'we are watching you' simple Chinese ve...   
2682  2013Mango leaf specimens無二無別  No difference Is...   
2683  音の彫刻 (literally 'sculpture of sound') is part ...   

     Introversion/Extraversion Intuitive/Observant Thinking/Feeling  \
0                  Introverted           Intuitive         Thinking   
1                  Introverted           Intuitive         Thinking   
2                  Introverted           Intuitive          Feeling   
3                  Introverted           Intuitive         Thinking   
4                  Introverted           Intuitive         Thinking   
...                        ...                 ...              ...   
2679               Introverted           Intuitive          Feeling   
2680               Introverted           Intuitive          Feeling   
2681               Introverted             Sensing         Thinking   
2682               Introverted           Intuitive         Thinking   
2683               Introverted           Intuitive         Thinking   

     Judging/Perceiving  
0            Perceiving  
1            Perceiving  
2            Perceiving  
3            Perceiving  
4            Perceiving  
...                 ...  
2679            Judging  
2680            Judging  
2681         Perceivi

In [4]:
#df.to_csv("Personality_Art.csv",index=False)
df = pd.read_csv("ArtFinalDF.csv")

In [131]:
#source: https://medium.com/analytics-vidhya/automated-keyword-extraction-from-articles-using-nlp-bfd864f41b34
import nltk
nltk.download('wordnet')
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
lem = WordNetLemmatizer()
stem = PorterStemmer()
word = "inversely"
print("stemming:",stem.stem(word))
print("lemmatization:", lem.lemmatize(word, "v"))

ModuleNotFoundError: No module named 'nltk'

In [130]:

import re
import nltk
#nltk.download('stopwords')
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from nltk.tokenize import RegexpTokenizer#nltk.download('wordnet') 
from nltk.stem.wordnet import WordNetLemmatizer

ModuleNotFoundError: No module named 'nltk'

In [7]:
##Creating a list of stop words and adding custom stopwords
stop_words = set(stopwords.words("english"))##Creating a list of custom stopwords
new_words = ["using", "show", "result", "large", "also", "iv", "one", "two", "new", "previously", "shown"]
stop_words = stop_words.union(new_words)

In [8]:
corpus = []
for i in range(0, len(df)):
    #Remove punctuations
    text = re.sub('[^a-zA-Z]', ' ', str(df['desc'][i]))
    
    #Convert to lowercase
    text = text.lower()
    
    #remove tags
    text=re.sub("&lt;/?.*?&gt;"," &lt;&gt; ",text)
    
    # remove special characters and digits
    text=re.sub("(\\d|\\W)+"," ",text)
    
    ##Convert to list from string
    text = text.split()
    
    ##Stemming
    ps=PorterStemmer()    #Lemmatisation
    lem = WordNetLemmatizer()
    text = [lem.lemmatize(word) for word in text if not word in  
            stop_words] 
    text = " ".join(text)
    corpus.append(text)

In [9]:
from sklearn.feature_extraction.text import CountVectorizer
import re
cv=CountVectorizer(max_df=0.8,stop_words=stop_words, max_features=10000, ngram_range=(1,3))
X=cv.fit_transform(corpus)

In [10]:
from sklearn.feature_extraction.text import TfidfTransformer
 
tfidf_transformer=TfidfTransformer(smooth_idf=True,use_idf=True)
tfidf_transformer.fit(X)# get feature names
feature_names=cv.get_feature_names()
 
# fetch document for which keywords needs to be extracted
out = []
for i in range(len(df)):
    #print(i)
    doc= df['desc'].values.astype('U')
    #print(doc)

    #generate tf-idf for the given document
    tf_idf_vector=tfidf_transformer.transform(cv.transform([doc[i]]))
    #Function for sorting tf_idf in descending order
    from scipy.sparse import coo_matrix
    def sort_coo(coo_matrix):
        tuples = zip(coo_matrix.col, coo_matrix.data)
        return sorted(tuples, key=lambda x: (x[1], x[0]), reverse=True)

    def extract_topn_from_vector(feature_names, sorted_items, topn=10):
        """get the feature names and tf-idf score of top n items"""

        #use only topn items from vector
        sorted_items = sorted_items[:topn]

        score_vals = []
        feature_vals = []

        # word index and corresponding tf-idf score
        for idx, score in sorted_items:

            #keep track of feature name and its corresponding score
            score_vals.append(round(score, 3))
            feature_vals.append(feature_names[idx])

        #create a tuples of feature,score
        #results = zip(feature_vals,score_vals)
        results= {}
        for idx in range(len(feature_vals)):
            results[feature_vals[idx]]=score_vals[idx]

        return results#sort the tf-idf vectors by descending order of scores
    sorted_items=sort_coo(tf_idf_vector.tocoo())#extract only the top n; n here is 10
    keywords=extract_topn_from_vector(feature_names,sorted_items,10)

    # now print the results
    #print("\nAbstract:")
    #print(doc)
    #print("\nKeywords:")
    keys = []
    for k in keywords:
        #print(k)
        keys.append(k)
    out.append(keys)

In [12]:
df['keywords'] = out
df

Unnamed: 0                                    Name Cost        Author  \
0              0                      //_path/untitled13   22     Mark Dorf   
1              1                       //_path/untitled9   24     Mark Dorf   
2              2  #NewAesthetic TV (Extended Play Remix)   30  Mark Amerika   
3              3                            1,000 Pounds   30   Sui Jianguo   
4              4                      100% Gray Coverage   35    Casey Reas   
...          ...                                     ...  ...           ...   
2679        2679             字苗-冥王星 Universe-Pluto(part)    8    Sting Chen   
2680        2680              字苗-金星 Universe-Venus(part)    8    Sting Chen   
2681        2681                                  我们在看着你    8        Type-O   
2682        2682                                    無二無別   20   viadmun low   
2683        2683                                    音の彫刻   15   Tony Broyez   

                                                   Link  \
0     https://www.seditionart.com/mark-dorf/_path-un...   
1     https://www.seditionart.com/mark-dorf/_path-un...   
2     https://www.seditionart.com/mark-amerika/newae...   
3     https://www.seditionart.com/sui_jianguo/1_000_...   
4     https://www.seditionart.com/casey_reas/100_gra...   
...                                                 ...   
2679  https://www.seditionart.com/sting-chen/univers...   
2680  https://www.seditionart.com/sting-chen/univers...   
2681  https://www.seditionart.com/type-o/b7a13c95-b1...   
2682  https://www.seditionart.com/viadmun_low_1/555b...   
2683  https://www.seditionart.com/tony-broyez/3c304e...   

                                                   desc  \
0     An examination of contemporary life in Western...   
1     An examination of contemporary life in Western...   
2     Mark Amerika’s short video piece #NewAesthetic...   
3     It certainly is not easy for a digital two-dim...   
4     Casey Reas’ 10 minutes digital video-piece 100...   
...                                                 ...   
2679                        字苗-冥王星 Universe-Pluto(part)   
2680                         字苗-金星 Universe-Venus(part)   
2681  我们在看着你 'we are watching you' simple Chinese ve...   
2682  2013Mango leaf specimens無二無別  No difference Is...   
2683  音の彫刻 (literally 'sculpture of sound') is part ...   

                                                  posts  \
0     An examination of contemporary life in Western...   
1     An examination of contemporary life in Western...   
2     Mark Amerika’s short video piece #NewAesthetic...   
3     It certainly is not easy for a digital two-dim...   
4     Casey Reas’ 10 minutes digital video-piece 100...   
...                                                 ...   
2679                        字苗-冥王星 Universe-Pluto(part)   
2680                         字苗-金星 Universe-Venus(part)   
2681  我们在看着你 'we are watching you' simple Chinese ve...   
2682  2013Mango leaf specimens無二無別  No difference Is...   
2683  音の彫刻 (literally 'sculpture of sound') is part ...   

     Introversion/Extraversion Intuitive/Observant Thinking/Feeling  \
0                  Introverted           Intuitive         Thinking   
1                  Introverted           Intuitive         Thinking   
2                  Introverted           Intuitive          Feeling   
3                  Introverted           Intuitive         Thinking   
4                  Introverted           Intuitive         Thinking   
...                        ...                 ...              ...   
2679               Introverted           Intuitive          Feeling   
2680               Introverted           Intuitive          Feeling   
2681               Introverted             Sensing         Thinking   
2682               Introverted           Intuitive         Thinking   
2683               Introverted           Intuitive         Thinking   

     Judging/Perceiving                                           keywords  


Unnamed: 0                                    Name Cost        Author  \
0              0                      //_path/untitled13   22     Mark Dorf   
1              1                       //_path/untitled9   24     Mark Dorf   
2              2  #NewAesthetic TV (Extended Play Remix)   30  Mark Amerika   
3              3                            1,000 Pounds   30   Sui Jianguo   
4              4                      100% Gray Coverage   35    Casey Reas   
...          ...                                     ...  ...           ...   
2679        2679             字苗-冥王星 Universe-Pluto(part)    8    Sting Chen   
2680        2680              字苗-金星 Universe-Venus(part)    8    Sting Chen   
2681        2681                                  我们在看着你    8        Type-O   
2682        2682                                    無二無別   20   viadmun low   
2683        2683                                    音の彫刻   15   Tony Broyez   

                                                   Link  \
0     https://www.seditionart.com/mark-dorf/_path-un...   
1     https://www.seditionart.com/mark-dorf/_path-un...   
2     https://www.seditionart.com/mark-amerika/newae...   
3     https://www.seditionart.com/sui_jianguo/1_000_...   
4     https://www.seditionart.com/casey_reas/100_gra...   
...                                                 ...   
2679  https://www.seditionart.com/sting-chen/univers...   
2680  https://www.seditionart.com/sting-chen/univers...   
2681  https://www.seditionart.com/type-o/b7a13c95-b1...   
2682  https://www.seditionart.com/viadmun_low_1/555b...   
2683  https://www.seditionart.com/tony-broyez/3c304e...   

                                                  posts  \
0     An examination of contemporary life in Western...   
1     An examination of contemporary life in Western...   
2     Mark Amerika’s short video piece #NewAesthetic...   
3     It certainly is not easy for a digital two-dim...   
4     Casey Reas’ 10 minutes digital video-piece 100...   
...                                                 ...   
2679                        字苗-冥王星 Universe-Pluto(part)   
2680                         字苗-金星 Universe-Venus(part)   
2681  我们在看着你 'we are watching you' simple Chinese ve...   
2682  2013Mango leaf specimens無二無別  No difference Is...   
2683  音の彫刻 (literally 'sculpture of sound') is part ...   

     Introversion/Extraversion Intuitive/Observant Thinking/Feeling  \
0                  Introverted           Intuitive         Thinking   
1                  Introverted           Intuitive         Thinking   
2                  Introverted           Intuitive          Feeling   
3                  Introverted           Intuitive         Thinking   
4                  Introverted           Intuitive         Thinking   
...                        ...                 ...              ...   
2679               Introverted           Intuitive          Feeling   
2680               Introverted           Intuitive          Feeling   
2681               Introverted             Sensing         Thinking   
2682               Introverted           Intuitive         Thinking   
2683               Introverted           Intuitive         Thinking   

     Judging/Perceiving                                           keywords  
0            Perceiving  ['dorf', 'technology', 'digital', 'language', ...  
1            Perceiving  ['dorf', 'technology', 'digital', 'language', ...  
2            Perceiving  ['amerika', 'remix', 'extended', 'glitch', 'co...  
3            Perceiving  ['baroque', 'exactly', 'decided', 'classic', '...  
4            Perceiving  ['reas', 'coverage', 'gray', 'collage engine',...  
...                 ...                                                ...  
2679            Judging                               ['universe', 'part']  
2680            Judging                      ['venus', 'universe', 'part']  
2681         Perceiving  ['privacy', 'erosion', 'playfully', 'reminds',...  
2682         Per

In [2]:
df = pd.read_csv("ArtFinalDF.csv")
df = df[df['Author'] != "Imran Qureshi"]
df = df[df['Cost'] != "Not for sale"]
# def removecommas(row):
#     return row.replace(',', '')
# df['Cost'] = df['Cost'].apply(removecommas)
df = df.drop(["Unnamed: 0" ,"Unnamed: 0.1","Unnamed: 0.1.1"],axis = 1)
df.to_csv("ArtFinalDF.csv",index = False)

/opt/conda/lib/python3.6/site-packages/pandas/core/ops.py:1167: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  result = method(y)


TypeError: invalid type comparison

In [177]:
df = pd.read_csv("ArtFinalDF.csv", dtype = {"Name":str,"Cost":int,"Author":str,"Link":str,"posts":str,"Introversion/Extraversion":str
                                           ,"Intuitive/Observant":str,"Thinking/Feeling":str,"Judging/Perceiving":str
                                           ,"keywords":"category","type":str})

In [178]:

# df.to_csv("ArtFinalDF.csv")
df.dtypes

Name                           object
Cost                            int64
Author                         object
Link                           object
posts                          object
Introversion/Extraversion      object
Intuitive/Observant            object
Thinking/Feeling               object
Judging/Perceiving             object
keywords                     category
dtype: object

In [179]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import LabelEncoder
import random
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import GradientBoostingClassifier

In [8]:
num_training = int(len(df) * 0.75)
num_testing = int(len(df) * 0.25)
# train['Type']='Train' #Create a flag for Train and Test Data set
# test['Type']='Test'
# fullData = pd.concat([train,test],axis=0) #Combined both Train and Test Data set

In [13]:
train_df = df[:num_training]
test_df = df[num_training:]

In [14]:
train_df = train_df.drop(['Author'], axis = 1)
test_df = test_df.drop(["Name","Author"],axis = 1)

In [15]:
train_df['Type']='Train' #Create a flag for Train and Test Data set
test_df['Type']='Test'

In [16]:
#pd.concat([train_df,test_df],axis=0)

In [17]:
fullData = pd.concat([train_df,test_df],axis=0) #Combined both Train and Test Data set

/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


In [19]:
#fullData['posts'] = fullData['posts'].dropna()

In [20]:
#fullData = fullData[fullData['Author'] != "Imran Qureshi"]
fullData = fullData[fullData['Cost'] != "Not for sale"]

In [88]:
ID_col = ["Link"]
target_col = ["Name"]
cat_cols = ['Introversion/Extraversion', 'Intuitive/Observant','Judging/Perceiving',
       'keywords', 'posts','Thinking/Feeling']
num_cols= list(set(list(df.columns))-set(df)-set(df)-set(df))
other_col=['Introversion/Extraversion', 'Intuitive/Observant','Judging/Perceiving','Thinking/Feeling'] #Test and Train Data set identifier

In [89]:
df

Name  Cost        Author  \
0                         //_path/untitled13    22     Mark Dorf   
1                          //_path/untitled9    24     Mark Dorf   
2     #NewAesthetic TV (Extended Play Remix)    30  Mark Amerika   
3                               1,000 Pounds    30   Sui Jianguo   
4                         100% Gray Coverage    35    Casey Reas   
...                                      ...   ...           ...   
2619             字苗-冥王星 Universe-Pluto(part)     8    Sting Chen   
2620              字苗-金星 Universe-Venus(part)     8    Sting Chen   
2621                                  我们在看着你     8        Type-O   
2622                                    無二無別    20   viadmun low   
2623                                    音の彫刻    15   Tony Broyez   

                                                   Link  \
0     https://www.seditionart.com/mark-dorf/_path-un...   
1     https://www.seditionart.com/mark-dorf/_path-un...   
2     https://www.seditionart.com/mark-amerika/newae...   
3     https://www.seditionart.com/sui_jianguo/1_000_...   
4     https://www.seditionart.com/casey_reas/100_gra...   
...                                                 ...   
2619  https://www.seditionart.com/sting-chen/univers...   
2620  https://www.seditionart.com/sting-chen/univers...   
2621  https://www.seditionart.com/type-o/b7a13c95-b1...   
2622  https://www.seditionart.com/viadmun_low_1/555b...   
2623  https://www.seditionart.com/tony-broyez/3c304e...   

                                                  posts  \
0     An examination of contemporary life in Western...   
1     An examination of contemporary life in Western...   
2     Mark Amerika’s short video piece #NewAesthetic...   
3     It certainly is not easy for a digital two-dim...   
4     Casey Reas’ 10 minutes digital video-piece 100...   
...                                                 ...   
2619                        字苗-冥王星 Universe-Pluto(part)   
2620                         字苗-金星 Universe-Venus(part)   
2621  我们在看着你 'we are watching you' simple Chinese ve...   
2622  2013Mango leaf specimens無二無別  No difference Is...   
2623  音の彫刻 (literally 'sculpture of sound') is part ...   

     Introversion/Extraversion Intuitive/Observant Thinking/Feeling  \
0                  Introverted           Intuitive         Thinking   
1                  Introverted           Intuitive         Thinking   
2                  Introverted           Intuitive          Feeling   
3                  Introverted           Intuitive         Thinking   
4                  Introverted           Intuitive         Thinking   
...                        ...                 ...              ...   
2619               Introverted           Intuitive          Feeling   
2620               Introverted           Intuitive          Feeling   
2621               Introverted             Sensing         Thinking   
2622               Introverted           Intuitive         Thinking   
2623               Introverted           Intuitive         Thinking   

     Judging/Perceiving                                           keywords  
0            Perceiving  ['dorf', 'technology', 'digital', 'language', ...  
1            Perceiving  ['dorf', 'technology', 'digital', 'language', ...  
2            Perceiving  ['amerika', 'remix', 'extended', 'glitch', 'co...  
3            Perceiving  ['baroque', 'exactly', 'decided', 'classic', '...  
4            Perceiving  ['reas', 'coverage', 'gray', 'collage engine',...  
...                 ...                                                ...  
2619            Judging                               ['universe', 'part']  
2620            Judging                      ['venus', 'universe', 'part']  
2621         Perceiving  ['privacy', 'erosion', 'playfully', 'reminds',...  
2622         Perceiving  ['buddhism', 'substitute', 'buddhist', 'writte...  
2623         Perceiving  ['audio', 'category', 'based', 'based visual',...  

[2624 rows x 10 columns]

In [90]:
num_cat_cols = num_cols+cat_cols # Combined numerical and Categorical variables

#Create a new variable for each variable having missing value with VariableName_NA 
# and flag missing value with 1 and other with 0

for var in num_cat_cols:
    if df[var].isnull().any()==True:
        df[var+'_NA']=df[var].isnull()*1 

In [91]:
#Impute numerical missing values with mean
#fullData[num_cols] = fullData[num_cols].fillna(fullData[num_cols].mean(),inplace=True)

In [92]:
df

Name  Cost        Author  \
0                         //_path/untitled13    22     Mark Dorf   
1                          //_path/untitled9    24     Mark Dorf   
2     #NewAesthetic TV (Extended Play Remix)    30  Mark Amerika   
3                               1,000 Pounds    30   Sui Jianguo   
4                         100% Gray Coverage    35    Casey Reas   
...                                      ...   ...           ...   
2619             字苗-冥王星 Universe-Pluto(part)     8    Sting Chen   
2620              字苗-金星 Universe-Venus(part)     8    Sting Chen   
2621                                  我们在看着你     8        Type-O   
2622                                    無二無別    20   viadmun low   
2623                                    音の彫刻    15   Tony Broyez   

                                                   Link  \
0     https://www.seditionart.com/mark-dorf/_path-un...   
1     https://www.seditionart.com/mark-dorf/_path-un...   
2     https://www.seditionart.com/mark-amerika/newae...   
3     https://www.seditionart.com/sui_jianguo/1_000_...   
4     https://www.seditionart.com/casey_reas/100_gra...   
...                                                 ...   
2619  https://www.seditionart.com/sting-chen/univers...   
2620  https://www.seditionart.com/sting-chen/univers...   
2621  https://www.seditionart.com/type-o/b7a13c95-b1...   
2622  https://www.seditionart.com/viadmun_low_1/555b...   
2623  https://www.seditionart.com/tony-broyez/3c304e...   

                                                  posts  \
0     An examination of contemporary life in Western...   
1     An examination of contemporary life in Western...   
2     Mark Amerika’s short video piece #NewAesthetic...   
3     It certainly is not easy for a digital two-dim...   
4     Casey Reas’ 10 minutes digital video-piece 100...   
...                                                 ...   
2619                        字苗-冥王星 Universe-Pluto(part)   
2620                         字苗-金星 Universe-Venus(part)   
2621  我们在看着你 'we are watching you' simple Chinese ve...   
2622  2013Mango leaf specimens無二無別  No difference Is...   
2623  音の彫刻 (literally 'sculpture of sound') is part ...   

     Introversion/Extraversion Intuitive/Observant Thinking/Feeling  \
0                  Introverted           Intuitive         Thinking   
1                  Introverted           Intuitive         Thinking   
2                  Introverted           Intuitive          Feeling   
3                  Introverted           Intuitive         Thinking   
4                  Introverted           Intuitive         Thinking   
...                        ...                 ...              ...   
2619               Introverted           Intuitive          Feeling   
2620               Introverted           Intuitive          Feeling   
2621               Introverted             Sensing         Thinking   
2622               Introverted           Intuitive         Thinking   
2623               Introverted           Intuitive         Thinking   

     Judging/Perceiving                                           keywords  
0            Perceiving  ['dorf', 'technology', 'digital', 'language', ...  
1            Perceiving  ['dorf', 'technology', 'digital', 'language', ...  
2            Perceiving  ['amerika', 'remix', 'extended', 'glitch', 'co...  
3            Perceiving  ['baroque', 'exactly', 'decided', 'classic', '...  
4            Perceiving  ['reas', 'coverage', 'gray', 'collage engine',...  
...                 ...                                                ...  
2619            Judging                               ['universe', 'part']  
2620            Judging                      ['venus', 'universe', 'part']  
2621         Perceiving  ['privacy', 'erosion', 'playfully', 'reminds',...  
2622         Perceiving  ['buddhism', 'substitute', 'buddhist', 'writte...  
2623         Perceiving  ['audio', 'category', 'based', 'based visual',...  

[2624 rows x 10 columns]

In [93]:
#Impute categorical missing values with -9999
#df[cat_cols] = df[cat_cols].fillna(value = -9999)

In [94]:
#create label encoders for categorical features
for var in cat_cols:
 number = LabelEncoder()
 df[var] = number.fit_transform(df[var].astype('str'))

#Target variable is also a categorical so convert it
df["Name"] = number.fit_transform(df["Name"].astype('str'))

# train=df[df['Type']==1]
# test=df[df['Type']==0]

# train['is_train'] = np.random.uniform(0, 1, len(train)) <= .75
# Train, Validate = train[train['is_train']==True], train[train['is_train']==False]

In [80]:
#features=list(set(list(fullData.columns))-set(ID_col)-set(target_col)-set(other_col))

NameError: name 'fullData' is not defined

In [29]:
x_train = Train[list(features)].values
y_train = Train["Name"].values
x_validate = Validate[list(features)].values
y_validate = Validate["Name"].values
x_test=test[list(features)].values
x_train

array([[1, 1, 0, ..., '22', 326, 1],
       [1, 1, 0, ..., '30', 1182, 0],
       [1, 1, 0, ..., '30', 1041, 1],
       ...,
       [1, 0, 0, ..., '26', 1176, 0],
       [1, 1, 1, ..., '8', 1256, 0],
       [1, 1, 0, ..., '8', 1355, 1]], dtype=object)

In [30]:
fullData[fullData.isin(["1,600"]).any(axis=1)]

Empty DataFrame
Columns: [Cost, Introversion/Extraversion, Intuitive/Observant, Judging/Perceiving, Link, Name, Thinking/Feeling, Type, keywords, posts]
Index: []

In [31]:
random.seed(100)
rf = RandomForestClassifier(n_estimators=50)
rf.fit(x_train, y_train)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=50,
                       n_jobs=None, oob_score=False, random_state=None,
                       verbose=0, warm_start=False)

In [32]:
from sklearn.metrics import roc_curve, auc
# status = rf.predict_proba(x_validate)
# fpr, tpr, _ = metrics.roc_curve(y_validate, status[:,1])
# roc_auc = auc(fpr, tpr)
# print(roc_auc)

final_status = rf.predict_proba(x_test)
test["Name"]=final_status[:,1]

/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [82]:
df

Name  Cost        Author  \
0     2109    22     Mark Dorf   
1     2120    24     Mark Dorf   
2     1932    30  Mark Amerika   
3     2276    30   Sui Jianguo   
4     2309    35    Casey Reas   
...    ...   ...           ...   
2619  1771     8    Sting Chen   
2620  1772     8    Sting Chen   
2621  1773     8        Type-O   
2622  1774    20   viadmun low   
2623  1775    15   Tony Broyez   

                                                   Link  posts  \
0     https://www.seditionart.com/mark-dorf/_path-un...   1608   
1     https://www.seditionart.com/mark-dorf/_path-un...   1608   
2     https://www.seditionart.com/mark-amerika/newae...    205   
3     https://www.seditionart.com/sui_jianguo/1_000_...     49   
4     https://www.seditionart.com/casey_reas/100_gra...   1769   
...                                                 ...    ...   
2619  https://www.seditionart.com/sting-chen/univers...   1499   
2620  https://www.seditionart.com/sting-chen/univers...   1500   
2621  https://www.seditionart.com/type-o/b7a13c95-b1...   1503   
2622  https://www.seditionart.com/viadmun_low_1/555b...    580   
2623  https://www.seditionart.com/tony-broyez/3c304e...   1507   

      Introversion/Extraversion  Intuitive/Observant  Thinking/Feeling  \
0                             1                    0                 1   
1                             1                    0                 1   
2                             1                    0                 0   
3                             1                    0                 1   
4                             1                    0                 1   
...                         ...                  ...               ...   
2619                          1                    0                 0   
2620                          1                    0                 0   
2621                          1                    1                 1   
2622                          1                    0                 1   
2623                          1                    0                 1   

      Judging/Perceiving  keywords  
0                      1      1507  
1                      1      1507  
2                      1      1469  
3                      1        80  
4                      1       527  
...                  ...       ...  
2619                   0      1026  
2620                   0      1065  
2621                   1       456  
2622                   1       768  
2623                   1      1991  

[2624 rows x 10 columns]

In [95]:
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline
corr = df.corr()
corr
# sns.heatmap(corr, 
#         xticklabels=corr.columns,
#         yticklabels=corr.columns)

Name      Cost     posts  \
Name                       1.000000 -0.005650  0.244673   
Cost                      -0.005650  1.000000  0.006292   
posts                      0.244673  0.006292  1.000000   
Introversion/Extraversion  0.021296 -0.006838 -0.017781   
Intuitive/Observant        0.019818 -0.025304  0.025962   
Thinking/Feeling           0.030900 -0.001992  0.062992   
Judging/Perceiving        -0.011623  0.001797 -0.000384   
keywords                   0.113035  0.030170  0.085411   

                           Introversion/Extraversion  Intuitive/Observant  \
Name                                        0.021296             0.019818   
Cost                                       -0.006838            -0.025304   
posts                                      -0.017781             0.025962   
Introversion/Extraversion                   1.000000            -0.011005   
Intuitive/Observant                        -0.011005             1.000000   
Thinking/Feeling                           -0.010396             0.058745   
Judging/Perceiving                         -0.002805             0.045120   
keywords                                    0.026628            -0.062621   

                           Thinking/Feeling  Judging/Perceiving  keywords  
Name                               0.030900           -0.011623  0.113035  
Cost                              -0.001992            0.001797  0.030170  
posts                              0.062992           -0.000384  0.085411  
Introversion/Extraversion         -0.010396           -0.002805  0.026628  
Intuitive/Observant                0.058745            0.045120 -0.062621  
Thinking/Feeling                   1.000000            0.002191 -0.011456  
Judging/Perceiving                 0.002191            1.000000 -0.007275  
keywords                          -0.011456           -0.007275  1.000000

In [181]:
from sklearn.model_selection import train_test_split
#download(sklearn.cross_validation)
#!source activate py36;pip install sklearn.modelselection
#import sys
#!conda install --yes --prefix {sys.prefix} sklearn.model_selection
import pandas as pd
import numpy as np
from patsy import dmatrices
import statsmodels.api as sm
from statsmodels.stats.outliers_influence import variance_inflation_factor
# train, test = train_test_split(df, test_size = 0.4)
# train = train.reset_index(drop=True)
# test = test.reset_index(drop=True)

# features_train = train[list(vif['Features'])]
# label_train = train['target']
# features_test = test[list(vif['Features'])]
# label_test = test['target']

In [182]:
def convert_IE(label):
    if (label == 'Introverted'):
        return 0.0
    elif (label == 'Extraverted'):
        return 1.0
    else:
        return label
def convert_IO(label):
    if (label == 'Intuitive'):
        return 0.0
    elif (label == 'Sensing'):
        return 1.0
    else:
        return label
def convert_TF(label):
    if (label == 'Thinking'):
        return 0.0
    elif (label == 'Feeling'):
        return 1.0
    else:
        return label
def convert_JP(label):
    if (label == 'Judging'):
        return 0.0
    elif (label == 'Perceiving'):
        return 1.0
    else:
        return label

In [183]:
df['Introversion/Extraversion'] = df['Introversion/Extraversion'].apply(convert_IE)
df['Intuitive/Observant'] = df['Intuitive/Observant'].apply(convert_IO)
df['Thinking/Feeling'] = df['Thinking/Feeling'].apply(convert_TF)
df['Judging/Perceiving'] = df['Judging/Perceiving'].apply(convert_JP)

In [184]:
X = df[["Introversion/Extraversion","Intuitive/Observant","Thinking/Feeling","Judging/Perceiving"]]
y = df.index

In [185]:
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import FunctionTransformer
from sklearn.preprocessing import OneHotEncoder
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer

from sklearn.tree import DecisionTreeRegressor
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsRegressor
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression

from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import FunctionTransformer
import matplotlib.pyplot as plt
import numpy as np
import os
import pandas as pd
import seaborn as sns
from sklearn.preprocessing import Binarizer 
from sklearn.preprocessing import QuantileTransformer
from sklearn.preprocessing import FunctionTransformer
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import NearestNeighbors
from sklearn.linear_model import LogisticRegressionCV
from sklearn.neighbors import NearestCentroid
%matplotlib inline
%config InlineBackend.figure_format = 'retina'  # Higher resolution figures
from sklearn.impute import SimpleImputer
from sklearn import metrics
pd.set_option('display.max_columns', 500)
import warnings
warnings.filterwarnings("ignore")

In [186]:
types = X.dtypes
outcols = types.loc[types == np.object].index
numcols = types.loc[types != np.object].index

In [10]:
outs = Pipeline([
    ('imp', SimpleImputer(strategy='constant', fill_value='NULL')),
    ('ohe', OneHotEncoder(handle_unknown='ignore', sparse=False)),
#    ('pca', PCA(svd_solver='full', n_components=0.99))
])

ct = ColumnTransformer([
    ('outcols', outs, outcols),
    ('numcols', SimpleImputer(strategy='constant', fill_value=0), numcols)
])

pl = Pipeline([('feats', ct), \
               ('reg', LogisticRegression())
              ])

In [72]:
def types(row0,row1,row2,row3):
    val = ""
    if (row0 == 0):
        val += "I"
    else:
        val += "E"
    if (row1 == 0):
        val += "N"
    else:
        val += "S"
    if (row0 == 0):
        val += "T"
    else:
        val += "F"
    if (row0 == 0):
        val += "J"
    else:
        val += "P"
    return val
outputs = []
for index,row in df[["Introversion/Extraversion","Intuitive/Observant","Thinking/Feeling","Judging/Perceiving"]].iterrows():
    #print(row["Introversion/Extraversion"])
    outputs.append(types(row['Introversion/Extraversion'],row['Intuitive/Observant'],row['Thinking/Feeling'],row['Judging/Perceiving']))


In [73]:
df['types'] = outputs

In [74]:
#vals = df['Introversion/Extraversion'] + df['Intuitive/Observant'] + df['Thinking/Feeling'] + df['Judging/Perceiving']
# 0000 = INTJ
# 1000 = ENTJ
# 1100 = ESTJ
# 1110 = ESFJ
# 1111 = ESFJ

In [90]:
import ast 
import json
res = [i.strip('[]').split(", ") for i in df['keywords']] 

In [132]:
flat_list = []
for sublist in res:
    for item in sublist:
        flat_list.append(item.replace("'", ""))
flat_list

['dorf',
 'technology',
 'digital',
 'language',
 'contemporary digital',
 'digital technology',
 'world',
 'contemporary',
 'landscape',
 'upon',
 'dorf',
 'technology',
 'digital',
 'language',
 'contemporary digital',
 'digital technology',
 'world',
 'contemporary',
 'landscape',
 'upon',
 'amerika',
 'remix',
 'extended',
 'glitch',
 'colorado',
 'airport',
 'video',
 'play',
 'tv',
 'short video',
 'baroque',
 'exactly',
 'decided',
 'classic',
 'material',
 'sculptural',
 'impact',
 'artist',
 'hand',
 'physical',
 'reas',
 'coverage',
 'gray',
 'collage engine',
 'engine',
 'collage',
 'television',
 'signal',
 'noise',
 'century',
 'china',
 'sculpture',
 'academy',
 'rapidly',
 'plain',
 'lettering',
 'global market',
 'digital frame',
 'tale',
 'toy',
 'photogrammetry',
 'casalegno',
 'technology',
 'dimensional',
 'animated',
 'three',
 'series presented',
 'traditionally',
 'presented three',
 'mattia casalegno',
 'real series',
 'iran',
 'behnam bakhtiar',
 'behnam',
 'ba

In [162]:
from collections import Counter
import numpy as np
import pandas as pd
from os import path
from PIL import Image
#from wordcloud import WordCloud, STOPWORDS, ImageColorGenerator
import sys
#print(sys.executable)
#/anaconda/bin/python -m pip install wordcloud

import matplotlib.pyplot as plt
counts = Counter(flat_list)
#counts = pd.DataFrame(counts,columns = ['word','value'])

#wordcloud = WordCloud().generate(flat_list)
word_out = pd.DataFrame.from_dict(counts, orient='index',columns = ['weight']).reset_index()
counts

Counter({'dorf': 2,
         'technology': 21,
         'digital': 141,
         'language': 13,
         'contemporary digital': 6,
         'digital technology': 2,
         'world': 35,
         'contemporary': 15,
         'landscape': 31,
         'upon': 4,
         'amerika': 2,
         'remix': 3,
         'extended': 5,
         'glitch': 24,
         'colorado': 3,
         'airport': 4,
         'video': 58,
         'play': 6,
         'tv': 7,
         'short video': 2,
         'baroque': 4,
         'exactly': 4,
         'decided': 2,
         'classic': 2,
         'material': 21,
         'sculptural': 4,
         'impact': 2,
         'artist': 45,
         'hand': 11,
         'physical': 15,
         'reas': 2,
         'coverage': 2,
         'gray': 2,
         'collage engine': 2,
         'engine': 3,
         'collage': 17,
         'television': 5,
         'signal': 6,
         'noise': 11,
         'century': 5,
         'china': 6,
         'sculpture': 3

In [170]:

# Iterate over key/value pairs in dict and print them
for key, value in counts.items():
    print(key,':',value)

dorf : 2
technology : 21
digital : 141
language : 13
contemporary digital : 6
digital technology : 2
world : 35
contemporary : 15
landscape : 31
upon : 4
amerika : 2
remix : 3
extended : 5
glitch : 24
colorado : 3
airport : 4
video : 58
play : 6
tv : 7
short video : 2
baroque : 4
exactly : 4
decided : 2
classic : 2
material : 21
sculptural : 4
impact : 2
artist : 45
hand : 11
physical : 15
reas : 2
coverage : 2
gray : 2
collage engine : 2
engine : 3
collage : 17
television : 5
signal : 6
noise : 11
century : 5
china : 6
sculpture : 31
academy : 3
rapidly : 4
plain : 3
lettering : 4
global market : 1
digital frame : 2
tale : 3
toy : 2
photogrammetry : 6
casalegno : 6
dimensional : 14
animated : 13
three : 25
series presented : 3
traditionally : 5
presented three : 3
mattia casalegno : 4
real series : 7
iran : 18
behnam bakhtiar : 18
behnam : 18
bakhtiar : 18
historical : 25
real : 44
work real series : 7
work real : 5
tapestry magnificent backdrop : 2
seashell : 1
pomegranate : 2
mornin

In [161]:
word_out['color'] = None
word_out['url'] = None
#word_out.index = word_out['weight']
word_out = word_out[['index','weight']]
word_out.to_csv("word_out.csv")

In [187]:
pl.fit(X_tr, y_tr)
pl.score(X_ts, y_ts)
pl.predict([[1,0,1,1]])

NameError: name 'X_tr' is not defined

In [13]:
X_tr, X_ts, y_tr, y_ts = train_test_split(X, y, test_size=0.25)

In [62]:
clf = DecisionTreeClassifier()

In [69]:
# preproc = ColumnTransformer(
#     transformers=[(
#         'ohe', OneHotEncoder(
#             handle_unknown='ignore'), [
#             'Author'])], 
#     remainder = 'passthrough')
pl = Pipeline(
                     [('regressor', clf)])
pl.fit(X, y)
pl.score(X_ts, y_ts)
arr = pl.predict_proba([[0,1,1,1]])
out = np.nonzero(arr)
out[1]
paintings = df.ix[list(out[1])]
list(paintings[paintings['Cost'] <= 20]['Name'])

['$$$',
 'A PRAYER FOR THE DAMNED',
 'Alex from Clockwork Orange (2013',
 'Amphibious Bird',
 'AZ001',
 'BEYOND LOVE, 2020',
 'BLEU CLAIR',
 'Caterpillars - Clean Cut',
 'COME AS YOU ARE, 2020',
 'Dubstep Dinosaurs',
 'Epoch',
 'ERROR N°01',
 'ERROR N°02',
 'EXACTLY THE SAME, 2020',
 'FASTEN SEAT BELTS',
 'GRIS CLAIR',
 'How Much Do You Want Me To Want You?',
 "Kundalinis' Warrior 2013",
 'Le palais Hasdrubal',
 'Lovely To Be Lovely',
 'Meadow',
 'Night Drive 1',
 'NOTHING IS STILL, 2019',
 'pink bible',
 'pink brain',
 'pink budda',
 'pussy',
 'Rachelle 2013',
 'represent',
 'RUNNING FROM THE LIGHT, 2020',
 'sexgame_2',
 'SIC TRANSIT GLORIA MUNDI',
 'SILVER DARKNESS',
 'Swimming Blu',
 'The Beatles (2013)',
 'THE INCEPTION',
 'TO INTERACT',
 'Untouchable',
 'WILL BE LOST, 2020']

In [171]:
df

Name  Cost        Author  \
0                         //_path/untitled13    22     Mark Dorf   
1                          //_path/untitled9    24     Mark Dorf   
2     #NewAesthetic TV (Extended Play Remix)    30  Mark Amerika   
3                               1,000 Pounds    30   Sui Jianguo   
4                         100% Gray Coverage    35    Casey Reas   
...                                      ...   ...           ...   
2619             字苗-冥王星 Universe-Pluto(part)     8    Sting Chen   
2620              字苗-金星 Universe-Venus(part)     8    Sting Chen   
2621                                  我们在看着你     8        Type-O   
2622                                    無二無別    20   viadmun low   
2623                                    音の彫刻    15   Tony Broyez   

                                                   Link  \
0     https://www.seditionart.com/mark-dorf/_path-un...   
1     https://www.seditionart.com/mark-dorf/_path-un...   
2     https://www.seditionart.com/mark-amerika/newae...   
3     https://www.seditionart.com/sui_jianguo/1_000_...   
4     https://www.seditionart.com/casey_reas/100_gra...   
...                                                 ...   
2619  https://www.seditionart.com/sting-chen/univers...   
2620  https://www.seditionart.com/sting-chen/univers...   
2621  https://www.seditionart.com/type-o/b7a13c95-b1...   
2622  https://www.seditionart.com/viadmun_low_1/555b...   
2623  https://www.seditionart.com/tony-broyez/3c304e...   

                                                  posts  \
0     An examination of contemporary life in Western...   
1     An examination of contemporary life in Western...   
2     Mark Amerika’s short video piece #NewAesthetic...   
3     It certainly is not easy for a digital two-dim...   
4     Casey Reas’ 10 minutes digital video-piece 100...   
...                                                 ...   
2619                        字苗-冥王星 Universe-Pluto(part)   
2620                         字苗-金星 Universe-Venus(part)   
2621  我们在看着你 'we are watching you' simple Chinese ve...   
2622  2013Mango leaf specimens無二無別  No difference Is...   
2623  音の彫刻 (literally 'sculpture of sound') is part ...   

      Introversion/Extraversion  Intuitive/Observant  Thinking/Feeling  \
0                           0.0                  0.0               0.0   
1                           0.0                  0.0               0.0   
2                           0.0                  0.0               1.0   
3                           0.0                  0.0               0.0   
4                           0.0                  0.0               0.0   
...                         ...                  ...               ...   
2619                        0.0                  0.0               1.0   
2620                        0.0                  0.0               1.0   
2621                        0.0                  1.0               0.0   
2622                        0.0                  0.0               0.0   
2623                        0.0                  0.0               0.0   

      Judging/Perceiving                                           keywords  \
0                    1.0  ['dorf', 'technology', 'digital', 'language', ...   
1                    1.0  ['dorf', 'technology', 'digital', 'language', ...   
2                    1.0  ['amerika', 'remix', 'extended', 'glitch', 'co...   
3                    1.0  ['baroque', 'exactly', 'decided', 'classic', '...   
4                    1.0  ['reas', 'coverage', 'gray', 'collage engine',...   
...                  ...                                                ...   
2619                 0.0                               ['universe', 'part']   
2620                 0.0                      ['venus', 'universe', 'part']   
2621                 1.0  ['privacy', 'erosion', 'playfully', 'reminds',...   
2622                 1.0  ['buddhism', 'substitute', 'buddhist', 'writte...   
2623                 1.0  ['audio', 'category',

In [188]:
from sklearn.neighbors import (NeighborhoodComponentsAnalysis,KNeighborsClassifier)

In [189]:
knn = KNeighborsClassifier(n_neighbors=10)
pl = Pipeline(
                     [('regressor', knn)])
pl.fit(X, y)
pl.score(X,y)
arr = pl.predict_proba([[1,1,1,1]])
out = np.nonzero(arr)
out[1]
paintings = df.ix[list(out[1])]
list(paintings[paintings['Cost'] <= 20]['Link'])

['https://www.seditionart.com/tripti/buddha-ecos',
 'https://www.seditionart.com/thomas-seher/melting-beauty',
 'https://www.seditionart.com/valery_radmirov/to-interact-1',
 'https://www.seditionart.com/darko_kriznik/untouchable',
 'https://www.seditionart.com/azamat-akhmadbaev/will-be-lost-2020']

In [20]:
arr = pl.predict_proba([[1,0,1,0]])
out = np.nonzero(arr)
out[1]
paintings = df.ix[list(out[1])]
list(paintings[paintings['Cost'] <= 20]['Link'])

['https://www.seditionart.com/tripti/buddha-ecos',
 'https://www.seditionart.com/arseny-vesnin/dripping-colours',
 'https://www.seditionart.com/laurentiu_todie/happybirthday',
 'https://www.seditionart.com/el-diputado/picnic-in-hampstead',
 'https://www.seditionart.com/digalando/render-wer',
 'https://www.seditionart.com/othniel-smith/the-poet-2',
 'https://www.seditionart.com/dr-sawsan-amin/the-return-of-super-man']

In [15]:
from sklearn.linear_model import SGDClassifier
clf = SGDClassifier(loss="modified_huber", penalty="l2", alpha = 0.001,max_iter=20)
pl = Pipeline(
                     [('regressor', clf)])
pl.fit(X, y)
#labels = model.predict(test.data)
arr = pl.predict_proba([[0,1,1,0]])
out = np.nonzero(arr)
out[1]
paintings = df.ix[list(out[1])]
list(paintings[paintings['Cost'] <= 20]['Name'])

['Fragments Of Here', 'Energy field #1 - Yellow Over Cycle']

In [131]:
import sys
import numpy
numpy.set_printoptions(threshold=sys.maxsize)

In [8]:
from sklearn.tree import DecisionTreeClassifier
from sklearn.naive_bayes import MultinomialNB

In [9]:
from sklearn.pipeline import Pipeline
text_clf = Pipeline([('vect', CountVectorizer()),('tfidf', TfidfTransformer()),('clf', MultinomialNB()),
])

In [26]:
text_clf.fit(df.posts, y)

Pipeline(memory=None,
         steps=[('vect',
                 CountVectorizer(analyzer='word', binary=False,
                                 decode_error='strict',
                                 dtype=<class 'numpy.int64'>, encoding='utf-8',
                                 input='content', lowercase=True, max_df=1.0,
                                 max_features=None, min_df=1,
                                 ngram_range=(1, 1), preprocessor=None,
                                 stop_words=None, strip_accents=None,
                                 token_pattern='(?u)\\b\\w\\w+\\b',
                                 tokenizer=None, vocabulary=None)),
                ('tfidf',
                 TfidfTransformer(norm='l2', smooth_idf=True,
                                  sublinear_tf=False, use_idf=True)),
                ('clf',
                 MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True))],
         verbose=False)

In [28]:
predicted = text_clf.predict(df.posts)
np.mean(predicted == y)

0.8689024390243902

In [32]:
from sklearn import metrics
print(metrics.classification_report(y, predicted,target_names=df.index))

TypeError: object of type 'int' has no len()

In [23]:
from sklearn.datasets import fetch_20newsgroups
twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)


In [22]:
categories = ['alt.atheism', 'soc.religion.christian','comp.graphics', 'sci.med']

In [25]:
twenty_train

{'data': ['From: sd345@city.ac.uk (Michael Collier)\nSubject: Converting images to HP LaserJet III?\nNntp-Posting-Host: hampton\nOrganization: The City University\nLines: 14\n\nDoes anyone know of a good way (standard PC application/PD utility) to\nconvert tif/img/tga files into LaserJet III format.  We would also like to\ndo the same, converting to HPGL (HP plotter) files.\n\nPlease email any response.\n\nIs this the correct group?\n\nThanks in advance.  Michael.\n-- \nMichael Collier (Programmer)                 The Computer Unit,\nEmail: M.P.Collier@uk.ac.city                The City University,\nTel: 071 477-8000 x3769                      London,\nFax: 071 477-8565                            EC1V 0HB.\n',
  "From: ani@ms.uky.edu (Aniruddha B. Deglurkar)\nSubject: help: Splitting a trimming region along a mesh \nOrganization: University Of Kentucky, Dept. of Math Sciences\nLines: 28\n\n\n\n\tHi,\n\n\tI have a problem, I hope some of the 'gurus' can help me solve.\n\n\tBackground of

In [33]:
>>> from sklearn.model_selection import GridSearchCV
>>> parameters = {'vect__ngram_range': [(1, 1), (1, 2)],'tfidf__use_idf': (True, False),'clf__alpha': (1e-2, 1e-3),}

In [42]:
gs_clf = GridSearchCV(text_clf, parameters, cv=2, n_jobs=-1)

In [44]:
gs_clf = gs_clf.fit(df.posts[:1000], y[:1000])

ValueError: n_splits=2 cannot be greater than the number of members in each class.